## Hot air balloon - lift calculator
### Box shape


In [86]:
# https://pythreejs.readthedocs.io
from pythreejs import *
from IPython.display import HTML,display
from math import pi

# https://ipywidgets.readthedocs.io
import ipywidgets as widgets
from ipywidgets import Layout

# https://pypi.org/project/termcolor/
from termcolor import colored

#from scipy.interpolate import interp1d
#import numpy as np

In [87]:
# air density–temperature relationship at 1 atm or 101.325 kPa
# https://en.wikipedia.org/wiki/Density_of_air
# https://www.engineersedge.com/calculators/air-density.htm
# temp in st.C   density in g/m3

#temp = [-25,-20,-15,-10,-5,0,5,10,15,20,25,30,35]
#dens = [1422.4,1394.3,1367.3,1341.3,1316.3,1292.2,1269.0,1246.6,1225.0,1204.1,1183.9,1164.4,1145.5]
#dens_temp_func = interp1d(temp, dens)


def airDensity(temp=0.0):
    tempK = temp + 273.0   # absolute temperature [K]
    p = 101325.0           # pressure [Pa]
    rSpec = 287.0500676    # specific gas constant for dry air [J⋅kg−1⋅K−1]
    return 1000.0 * p / ( rSpec * tempK )

In [ ]:
def f(width,height,depth,airTemp,hotAirTemp,coatDens):
    print("\n")
# Volume
    volume = width * height * depth
    print( "Volume: {:.2f} [m3]".format(volume)) 
# Area
    area = 2 * (width * height + width * depth + height * depth)
    print( "Area: {:.2f} [m2]".format(area)) 
# Coating density 300g / 4x5m = 15g/m2
#    coatingDensity = 15.0
#    print( "Coating density: {:.2f} [g/m2]".format(coatingDensity))     
    coatingWeight = coatDens * area
    print( "Coating weight: {:.2f} [g]".format(coatingWeight))   
# Lift per volume g/m3  
#    airDens = dens_temp_func( airTemp )
#    hotAirDens = dens_temp_func( hotAirTemp )    
    airDens = airDensity( airTemp )
    hotAirDens = airDensity( hotAirTemp )  
    lift = airDens - hotAirDens
    print( "Lift: {:.2f} [g/m3]".format(lift))      
# Total lift force  lift * volume 
    totalLiftForce = lift * volume
    print( "Total lift force: {:.2f} [g]".format(totalLiftForce))    
# Free lift force totalLiftForce - coatingWeight 
    freeLiftForce = totalLiftForce - coatingWeight
    if freeLiftForce < 0:
        color = 'red'
    else:
        color = None
    print( "Free lift force:", colored("{:.2f} [g]".format(freeLiftForce),color))  
    print("\n")

    box = Mesh(geometry=BoxBufferGeometry(
                            width=width, 
                            height=height, 
                            depth=depth,
                            widthSegments=5, 
                            heightSegments=10,
                            depthSegments=15),
                material=MeshLambertMaterial(color='gray')
               )
    keyLight = DirectionalLight(color='white', position=[3, 5, 1], intensity=0.5)

    c = PerspectiveCamera(position=[2, 2, 5], up=[0, 1, 0], children=[keyLight])

    scene = Scene(children=[box, c, AmbientLight(color='#777777')], background=None)

    renderer = Renderer(camera=c,
                        scene=scene,
                        alpha=True,
                        clearOpacity=1.0,
                        clearColor='#62a0ea',
                        controls=[OrbitControls(controlling=c)])
    return renderer

#display(HTML('''<style>
#    .widget-label { min-width: 25ex !important; }
#</style>'''))

layout=Layout(width='500px')
style = {'description_width': 'initial'}
    
widgets.interact(f, 
    width=widgets.FloatSlider(min=0.1, max=5.0, step=0.1, value=2.0, description='Width [m]:',readout_format='.1f',layout=layout,style=style), 
    height=widgets.FloatSlider(min=0.1, max=5.0, step=0.1, value=2.0, description='Height [m]:',readout_format='.1f',layout=layout,style=style), 
    depth=widgets.FloatSlider(min=0.1, max=5.0, step=0.1, value=2.0, description='Depth [m]:',readout_format='.1f',layout=layout,style=style),
    airTemp=widgets.FloatSlider(min=-40, max=35, step=1.0, value=10.0, description='Air temp.[°C]:',readout_format='.0f',layout=layout,style=style), 
    hotAirTemp=widgets.FloatSlider(min=-40, max=55, step=1.0, value=35.0, description='Hot air temp.[°C]:',readout_format='.0f',layout=layout,style=style),
    coatDens=widgets.FloatSlider(min=1, max=50, step=1.0, value=15.0, description='Coating density [g/m2]:',readout_format='.0f',layout=layout,style=style)                  
                );
